In [39]:
import tensorflow as tf
physical_devices = tf.config.list_physical_devices('GPU')
print("Num GPUs Available: ", len(physical_devices))

tf.config.experimental.set_memory_growth(physical_devices[0], enable=True)

Num GPUs Available:  1


In [40]:
print(tf.__version__)

2.3.0


In [41]:
from collections import Counter
import numpy as np
import pandas as pd 
import os
import time
import math
import statistics
from datetime import datetime
import random as rn
import matplotlib.pyplot as plt
import plotly.express as px
from tqdm.notebook import tqdm
import sweetviz as sv

# from keras.models import Sequential
# from keras.layers import Dense
# from keras.layers import Dropout
# from keras.layers import LSTM
# from keras.layers import Conv2D, AvgPool2D, MaxPool2D, Flatten
import keras
from IPython.display import clear_output


from data_set_builder import data_set_builder
from create_lstm_train_test import transform_df_to_LSTM_train_test


In [42]:
def predictions_vs_actual(predictions, y_test):
    try:
        y_test = y_test.reshape(y_test.shape[0],)
        predictions = predictions.reshape(len(predictions),)
    except: 
        print("y_test       shape: {} ".format(y_test.shape))
        print("predictions  shape: {} ".format(predictions.shape))
    df = pd.DataFrame({'Target':y_test ,'Predictions': predictions })
    df['Difference'] = df['Predictions'] - df['Target'] 
    return df


def plot_predictions(input_df):
    results_df = input_df.reset_index()
    fig = px.line(results_df, x="index", y=[col for col in results_df if col not in ['index', 'Difference']], 
                  title="Predictions vs. Target")
    fig.show()
    
    
def plot_predictions_difference(input_df):
    results_df = input_df.reset_index()
    fig = px.line(results_df, x="index", y=[col for col in results_df if col not in ['index', 'Target', 'Predictions']], 
                  title="Predictions - Target ")
    fig.show()
    
def plot_trading_simulation(total_pips_gained, dates_traded):
    
    cumulative_pips_gained = [0]
    for idx,pips in enumerate(total_pips_gained):
        new_val = pips + cumulative_pips_gained[idx]
        cumulative_pips_gained.append(new_val)
        
    print("dates_traded: ", len(dates_traded))
    print("cumulative_pips_gained: ", len(cumulative_pips_gained))
    
    df = pd.DataFrame({'Dates': dates_traded ,'Cumulative Pips Gained':  cumulative_pips_gained })
    fig = px.line(df, x="Dates", y="Cumulative Pips Gained", 
                  title="Cumulative Pips Gained")
    fig.show()
    


In [43]:
def load_OHLC_data_with_date_as_index(fx_pair, years):
    for idx,year in enumerate(years):
        if idx == 0:
            df = pd.read_csv(f"../Data/Cleaned_OHLC_FOREX_Data_10_min/{fx_pair}/{fx_pair}_{year}_10min.csv").drop(columns =['Unnamed: 0'])
        else:
            temp_df = pd.read_csv(f"../Data/Cleaned_OHLC_FOREX_Data_10_min/{fx_pair}/{fx_pair}_{year}_10min.csv").drop(columns =['Unnamed: 0'])
            df = pd.concat([df, temp_df], ignore_index = True)    
        
    df.reset_index(inplace = True)
    df.set_index("Date_time", inplace = True)
    return df 


load_OHLC_data_with_date_as_index("EURUSD", [2019])

index     Open     High      Low    Close
Date_time                                                     
2019-01-01 17:10:00      0  1.14607  1.14617  1.14606  1.14606
2019-01-01 17:20:00      1  1.14607  1.14616  1.14604  1.14611
2019-01-01 17:30:00      2  1.14611  1.14618  1.14606  1.14606
2019-01-01 17:40:00      3  1.14605  1.14635  1.14603  1.14617
2019-01-01 17:50:00      4  1.14619  1.14643  1.14602  1.14606
...                    ...      ...      ...      ...      ...
2019-12-31 16:10:00  37266  1.12142  1.12149  1.12141  1.12142
2019-12-31 16:20:00  37267  1.12141  1.12149  1.12138  1.12143
2019-12-31 16:30:00  37268  1.12143  1.12151  1.12137  1.12139
2019-12-31 16:40:00  37269  1.12139  1.12146  1.12122  1.12133
2019-12-31 16:50:00  37270  1.12133  1.12136  1.12076  1.12076

[37271 rows x 5 columns]

In [44]:
def load_LSTM_test_data(model_type, window_size, future_candles, return_dates = False ):
    """
    model_type: LSTM or CNN
    """
    
    test_df  = data_set_builder('EURUSD', [i for i in range(2020,2021)], future_candles)
    train_df = test_df.loc[:120,:] # The train data is not being used!
    
    if return_dates:
        X_train, X_val, X_test, y_train, y_val, y_test, y_test_dates = transform_df_to_LSTM_train_test(train_df, test_df, future_candles, 
                                                                              window_size, return_dates)
    else:
        X_train, X_val, X_test, y_train, y_val, y_test = transform_df_to_LSTM_train_test(train_df, test_df, future_candles, 
                                                                                    window_size)
    
    if model_type == "CNN":
        # CNN specified input shape (only test data)
        X_test  = X_test.reshape(X_test.shape[0] , X_test.shape[1], X_test.shape[2], 1)
    
    if return_dates:
        return X_test, y_test , y_test_dates
    else: 
        return X_test, y_test

In [45]:
   
    
def load_target_and_predictions(model_folder, model_type, return_results = False, return_dates = False):
    """
    model_folder: an int describing model number
    """
    
    global all_models_folder
    
    results_file = all_models_folder + model_folder + "/y_test_y_pred.csv"
    
    with open(all_models_folder + model_folder + "/model_report.txt") as file:
        input_layer_nodes, h_layer_1_nodes, h_layer_2_nodes, h_layer_3_nodes = 0,0,0,0

        for line_idx,line in enumerate(file): 
            split_line = line.split(" ")
            if line_idx == 0: 
                main_loss_val = split_line[3].strip("Loss:")
                mae = split_line[5].strip("MAE:")
                mse = split_line[7].strip("MSE:")
                mape = split_line[9].strip("MAPE:")
                loss_func_names = ['MAE', 'MSE', 'MAPE']
                for loss_idx,temp_loss_val in enumerate([mae,mse, mape]):
                    if temp_loss_val == main_loss_val:
                        loss_func_name = loss_func_names[loss_idx]
                print(f"mae [{mae}] mse [{mse}] mape [{mape}] loss_func_name [{loss_func_name}] loss_func_val[{main_loss_val}]")

            elif line_idx == 1:
                opt = split_line[1]
                learning_rate = split_line[4]
                dense_layer = split_line[8]
                print(f"opt [{opt}] lr [{learning_rate}] dense layer : [{dense_layer}]")
            elif line_idx == 2:
                future_candles = int(split_line[1])
                window_size = int(split_line[4])
                dropout = split_line[7]
                print(f"Candles [{future_candles}] window_size [{window_size}] dropout [{dropout}]")
            elif line_idx == 3:
                epochs = split_line[1]
                batch_size = split_line[4]
                run_time = (" ").join(split_line[7:11])

                print(f"Epochs [{epochs}] Batch_size [{batch_size}] run_time [{run_time}]")
            elif line_idx >= 4:
                #print("IDX: {} line: {}".format(line_idx,line))
                #print("IDX: {} line[28:-21]: {}".format(line_idx, line[28:-21]))
                if model_type == "LSTM":
                    if "input_layer_LSTM" in line:
                        input_layer_nodes = eval(line[28:-21])[-1]
                        #print("Tuple of interest" , eval(line[28:-21])[-1])
                    elif "1_h_layer_LSTM" in line: 
                        h_layer_1_nodes = eval(line[28:-21])[-1]
                        #print("Tuple of interest" ,eval(line[28:-21])[-1])
                    elif "2_h_layer_LSTM" in line: 
                        h_layer_2_nodes = eval(line[28:-21])[-1]
                        #print("Tuple of interest" ,eval(line[28:-21])[-1])
                    elif "3_h_layer_LSTM" in line: 
                        h_layer_3_nodes = eval(line[28:-21])[-1]
                        #print("Tuple of interest" ,eval(line[28:-21])[-1])
                    else:
                        pass

                if model_type == "CNN":
                    if "Stride" in line: 
                        activation_func = split_line[4]
                        print("activation_func: ", activation_func)
                    
                    elif "input_layer_CONV" in line:
                        input_layer_nodes = eval(line[28:-18])[-1]
                        #print("Tuple of interest" , eval(line[28:-21])[-1])
                    elif "1_h_layer_CONV" in line: 
                        h_layer_1_nodes = eval(line[28:-18])[-1]
                        #print("Tuple of interest" ,eval(line[28:-21])[-1])
                    elif "2_h_layer_CONV" in line: 
                        h_layer_2_nodes = eval(line[28:-18])[-1]
                        #print("Tuple of interest" ,eval(line[28:-21])[-1])
                    else:
                        pass                         
    
    
    if os.path.isfile(results_file):
        df = pd.read_csv(results_file)
        y_test,y_pred = df['y_test'] , df['y_pred'] 
        
        
    else :
        X_test, y_test = load_LSTM_test_data(model_type, window_size, future_candles)

        model_name = model_folder.lower() + ".h5"
        model = keras.models.load_model(all_models_folder + model_folder + "/" + model_name)

        y_pred = [y[0] for y in model.predict(X_test)]

        print("y_pred[:10] : ", y_pred[:10])
        print("y_test[:10] : ", y_test[:10])
        print()
        print("len(y_pred) :",len(y_pred))
        print("len(y_test) :",len(y_test))
        print("len(X_test) :",len(X_test))
        
        df = pd.DataFrame({'y_test' : y_test,
                           'y_pred':  y_pred})

        df.to_csv(results_file)

    if return_results:
        if model_type == "LSTM":
            return {"Model_number" : model_folder.replace("Model_", ""),
                    "MAE": mae,
                    "MSE": mse,
                    "MAPE": mape,
                   "Loss Function" : loss_func_name,
                   "Optimizer": opt,
                   "Learning Rate": learning_rate,
                   "Future_candles": future_candles,
                   "Window_size": window_size,
                   "Dropout": dropout,
                   "Epochs": epochs,
                   "Batch Size": batch_size,
                   "Runtime": run_time,
                   "Model type": model_type,
                   "Number of hidden layers": sum([bool(i) for i in [h_layer_1_nodes, h_layer_2_nodes, h_layer_3_nodes]])  ,
                   "input_layer_LSTM" :   input_layer_nodes,
                   "1_h_layer_LSTM_nodes" : h_layer_1_nodes,
                   "2_h_layer_LSTM_nodes" : h_layer_2_nodes,
                   "3_h_layer_LSTM_nodes" : h_layer_3_nodes,
                   "Dense Layer"          : dense_layer}
        
        if model_type == "CNN":
            return {"Model_number" : model_folder.replace("Model_", ""),
                    "MAE": mae,
                    "MSE": mse,
                    "MAPE": mape,
                   "Loss Function" : loss_func_name,
                   "Optimizer": opt,
                   "Learning Rate": learning_rate,
                   "Future_candles": future_candles,
                   "Window_size": window_size,
                   "Activation_function": activation_func,
                   "Epochs": epochs,
                   "Batch Size": batch_size,
                   "Runtime": run_time,
                   "Model type": model_type,
                   "Number of hidden layers": sum([bool(i) for i in [h_layer_1_nodes, h_layer_2_nodes, h_layer_3_nodes]])  ,
                   "input_layer_CONV": input_layer_nodes ,
                   "1_h_layer_CONV_filters": h_layer_1_nodes,
                   "2_h_layer_CONV_filters": h_layer_2_nodes,
                   "3_h_layer_CONV_filters": h_layer_3_nodes,
                    "Dense Layer"          : dense_layer}
            
    else:
        if return_dates:
            not_used_X_test, not_used_y_test, y_dates = load_LSTM_test_data(model_type, window_size, future_candles, return_dates = True)
            return y_test, y_pred, y_dates
        else:
            return y_test,y_pred 
    
#model_type = "LSTM"
#for model_type in ["LSTM", "CNN"]:
for model_type in ["CNN", 'LSTM']:
    all_models_folder = f"Saved_models/{model_type}_models/"
    for model_folder in os.listdir(all_models_folder):
        print(model_folder)
        if "." in model_folder:
            continue
        y_test,y_pred = load_target_and_predictions(model_folder, model_type, return_results = False)
        clear_output(wait=True)
#     print("\n"*2)

Model_9
mae [14.0106821060] mse [419.9223327637] mape [32271278.0000000000] loss_func_name [MSE] loss_func_val[419.9223327637]
opt [Adamax] lr [0.00300] dense layer : [1]
Candles [12] window_size [12] dropout [0.1]
Epochs [202] Batch_size [128] run_time [45 min 43 seconds]


# FOREX  Trading Simulator



In [94]:
ohlc_df = load_OHLC_data_with_date_as_index("EURUSD", [2020]) 

def check_stop_loss(cur_date_time, future_candles, buy_sell, stop_loss_tolerence_in_pips):
    global ohlc_df
    
    stop_loss_tolerence = stop_loss_tolerence_in_pips*0.0001
    
    # Changin cur_date_time_foramt 
    cur_date_time = cur_date_time[:10] + " " + cur_date_time[11:] + ":00"
    
    # the next candle, will be checked after our entry, as we start a trade on the close
    start_index = int(ohlc_df.loc[cur_date_time]['index']) 
    
    entry_price = ohlc_df.loc[cur_date_time]['Close']
    
    
    sub_df = ohlc_df[ohlc_df['index']> start_index]
    sub_df = sub_df[sub_df['index'] < start_index + future_candles +1] 
    # Manually checked this, the last instance of the sub DF, corresponds to the candle which the trade closes at.
    
    if buy_sell == "buy":
        for low in sub_df['Low']:
            if low < entry_price-stop_loss_tolerence:
                print("Entry price: ", entry_price)
                print(f"stop loss activated, low: {low}")
                return True
        
    elif buy_sell == "sell":
        for high in sub_df['High']:
            if high > entry_price+stop_loss_tolerence:
                print("Entry price: ", entry_price)
                print(f"stop loss activated, high: {high}")
                return True
    
    return False 


print(check_stop_loss("2020-01-23T10:00", 12 , "buy", 5))
print("")
print(check_stop_loss("2020-01-23T10:00", 12 , "buy", 30))

Entry price:  1.10625
stop loss activated, low: 1.10555
True

False


In [92]:
def FOREX_simulator(model_folder, test_year, y_test , y_pred , y_dates,
                    future_candles , export_csv_results=False, view_single_setup = False, verbose = False):
    """
    This implementation takes a stop loss at 15 pips.
    The stop loss is activated if the low of a future candle fall below 15 pips of the original entry price.
    This emulates monitoring of live data.
    """
    
    global all_models_folder
    stop_loss = 20
    
    temp_start = time.time()
    
    
    pred_mean = sum(y_pred)/len(y_pred)
    y_pred_std = statistics.stdev(y_pred)
    y_test_mean = sum(y_test)/len(y_test)
    
    if y_pred_std == 0:
        y_pred_std = 0.0000001
    
    spread = 4 # 4 pips (target changed to pips)
    
    threshold_1, threshold_2, threshold_3, threshold_4 =  y_pred_std , y_pred_std*2 , y_pred_std*3 ,  y_pred_std*4 
    print("")
    print("pred_mean: ", pred_mean)
    print(f"threshold_1: {threshold_1} , threshold_2: {threshold_2} , threshold_3: {threshold_3} , threshold_4: {threshold_4} ")
    
    
    trading_results_dict = {"Model_number" : int(model_folder.replace("Model_", "")),
                            "threshold" : 0,
                            "total_pips_gained": 0,
                            "total_pips_traded": 0,
                            "future_candles" : future_candles,
                            "pips_gained_pr_trade" : 0,
                            "wins": 0,
                            "losses": 0,
                            "total_trades": 0}
    
    forex_sim_df = pd.DataFrame(columns = ["Model_number" ,
                            "threshold",
                            "total_pips_gained",
                            "total_pips_traded",
                            "future_candles",
                            "pips_gained_pr_trade",
                            "wins",
                            "losses",
                            "total_trades"])
    
    threshold_results_dict = {f"threshold_{i+1}": trading_results_dict.copy() for i in range(4)}
    list_of_total_pips_gained = []
    list_of_trading_dates = []
    
    for thresh_idx, threshold in enumerate([threshold_1, threshold_2, threshold_3, threshold_4]):
        thresh_idx += 1
        
        if verbose:
            print(f"\nInitiating trading with threshold {thresh_idx}\n")
        
        total_pips_traded, total_pips_gained = [],[]
        dates_traded = ['2020-01-01T00:00']
        trade_active_timer = 0
        
        for idx,pred_price in enumerate(y_pred):
            if trade_active_timer > 0:
                trade_active_timer -= 1
                continue
            if (idx <= future_candles) or (idx >= (len(y_pred) - future_candles)):
                continue # trade simulation either to early or over.  
                
            y_price = y_test[idx]
            if pred_price > (pred_mean + threshold):
                # Buy
                trade_active_timer = future_candles
                
                if check_stop_loss(y_dates[idx], future_candles, "buy", stop_loss): # If true, stoploss activates.
                    pips_gained = -stop_loss - (spread/2)
                else:
                    pips_gained = y_test[idx] - (spread/2)
                
                # Round pips 
                pips_gained = round(pips_gained,2)
                
                total_pips_gained.append(pips_gained)
                total_pips_traded.append(abs(pips_gained))
                if verbose:
                    dates_traded.append(y_dates[idx])
                    print(f"BUY taken af idx: {idx}  date: {y_dates[idx]}  pips gained: {pips_gained} ")# Raw Target: {y_test[idx]} ")

            elif pred_price < (pred_mean - threshold):
                # Sell
                trade_active_timer = future_candles 
                
                if check_stop_loss(y_dates[idx], future_candles, "sell", stop_loss): # If true, stoploss activates.
                    pips_gained = -stop_loss - (spread/2)
                else:
                    pips_gained = -(y_test[idx] ) - (spread/2)
                
                # Round pips.
                pips_gained = round(pips_gained,2)
                
                total_pips_gained.append(pips_gained)
                total_pips_traded.append(abs(pips_gained))
                
                if verbose:
                    dates_traded.append(y_dates[idx])
                    print(f"SELL taken af idx: {idx}  date: {y_dates[idx]}  pips gained: {pips_gained} ") #Raw Target: {y_test[idx]} ")
                
            else: 
                # HODL
                pass
            
        if verbose:
            print("\n Total trades taken: {}  Wins: {}  Loss: {}  ".format(
                    len(total_pips_gained),
                    sum([1 if i > 0 else 0 for i in total_pips_gained]),
                    sum([1 if i <= 0 else 0 for i in total_pips_gained])))
            print(" pips gained: {}  pips traded: {}  pip_ratio: {}".format(
            sum(total_pips_gained), sum(total_pips_traded), sum(total_pips_gained)/sum(total_pips_traded)))
 
        if len(total_pips_gained) == 0:
            total_pips_gained.append(0)
            total_pips_traded.append(0.1) # to avoid division by 0 error.
             
        list_of_total_pips_gained.append(total_pips_gained)
        list_of_trading_dates.append(dates_traded)
        
        threshold_results_dict[f'threshold_{thresh_idx}']['total_pips_gained'] = sum(total_pips_gained)
        threshold_results_dict[f'threshold_{thresh_idx}']['total_pips_traded'] = sum(total_pips_traded)
        threshold_results_dict[f'threshold_{thresh_idx}']['wins']     = sum([1 if i > 0 else 0 for i in total_pips_gained])
        threshold_results_dict[f'threshold_{thresh_idx}']['losses']   = sum([1 if i < 0 else 0 for i in total_pips_gained]) 
        threshold_results_dict[f'threshold_{thresh_idx}']['total_trades'] = sum([1 for i in total_pips_gained])
        threshold_results_dict[f'threshold_{thresh_idx}']['pip_ratio'] = sum(total_pips_gained) / sum(total_pips_traded)
        threshold_results_dict[f'threshold_{thresh_idx}']['threshold'] = thresh_idx
        threshold_results_dict[f'threshold_{thresh_idx}']['threshold_value'] = threshold
        
        forex_sim_df = forex_sim_df.append(threshold_results_dict[f'threshold_{thresh_idx}'], ignore_index=True)
        
    if view_single_setup:
        best_threshold = -999999
        best_total_pips_gained = -999999
        best_list_from_total_pips_gained = []
        best_dates_traded = []
        
        for thresh_idx,total_pips_gained in enumerate(list_of_total_pips_gained):
            thresh_idx += 1
            if sum(total_pips_gained) > best_total_pips_gained:
                best_total_pips_gained = sum(total_pips_gained)
                best_threshold = thresh_idx
                best_list_from_total_pips_gained = total_pips_gained
                best_dates_traded = list_of_trading_dates[thresh_idx-1]
        
        # Plot 
        threshold_std = threshold_results_dict[f'threshold_{best_threshold}']['threshold_value']
        print(f"The best threshold was #{best_threshold}")   
        print(f" Threshold values:  LONG SIGNAL: {pred_mean+threshold_std}  SHORT SIGNAL: {pred_mean-threshold_std}")
        print("")
        plot_trading_simulation(best_list_from_total_pips_gained, best_dates_traded)   
        return None
        
    forex_sim_df.to_excel(all_models_folder + model_folder + "/FOREX_simulated_trades_info.xlsx")
        
    return threshold_results_dict



# LSTM and CNN models


In [93]:
# Seeing results of specific models Prediction vs. Label for Perceptron

model_type = "LSTM"
model_folder = "Model_96"
hyper_param_iter = "1st"
all_models_folder = f"Saved_models\\{model_type}_models_{hyper_param_iter}_iter\\"

# model_type = "CNN"
# model_folder = "Model_87"
# hyper_param_iter = "1st"
# all_models_folder = f"Saved_models\\{model_type}_models_{hyper_param_iter}_iter\\"


df = pd.read_csv(all_models_folder + model_folder+ "\\y_test_y_pred.csv")

predictions = df['y_pred']
y_test = df['y_test']

df = predictions_vs_actual(predictions, y_test)
plot_predictions(df)




model_dict = load_target_and_predictions(model_folder, model_type, return_results =True)
y_test, y_pred, y_dates = load_target_and_predictions(model_folder, model_type, return_results =False, return_dates = True)

print(model_dict)

future_candles = model_dict['Future_candles']

threshold_results_dict = FOREX_simulator(model_folder, 2020, y_test, y_pred, y_dates ,future_candles, 
                                         export_csv_results=False , view_single_setup = True, verbose = True)


y_test       shape: (36718,) 
predictions  shape: (36718,) 


  0%|          | 0/1 [00:00<?, ?it/s]

mae [12.9823379517] mse [341.8295288086] mape [27132878.0000000000] loss_func_name [MAE] loss_func_val[12.9823379517]
opt [Adamax] lr [0.00100] dense layer : [1]
Candles [12] window_size [12] dropout [0.2]
Epochs [75] Batch_size [256] run_time [12 min 15 seconds]
mae [12.9823379517] mse [341.8295288086] mape [27132878.0000000000] loss_func_name [MAE] loss_func_val[12.9823379517]
opt [Adamax] lr [0.00100] dense layer : [1]
Candles [12] window_size [12] dropout [0.2]
Epochs [75] Batch_size [256] run_time [12 min 15 seconds]


100%|██████████| 1/1 [00:01<00:00,  1.94s/it]
C:\OneDrive\Dokumenter\Skole\Universitet (ITU)\6th Semester\Bachelor Project V2\Machine Learning\create_lstm_train_test.py:28: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

C:\OneDrive\Dokumenter\Skole\Universitet (ITU)\6th Semester\Bachelor Project V2\Machine Learning\create_lstm_train_test.py:31: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

Test, creating Continous: 100%|██████████| 37377/37377 [00:01<00:00, 37032.56it/s]
C:\ProgramData\Anaconda3\lib\site-pac


LSTM_y_train.shape:  (87,)
LSTM_X_train.shape:  (87, 12, 98)

LSTM_y_val.shape:  (22,)
LSTM_X_val.shape:  (22, 12, 98)

LSTM_y_test.shape:  (36718,)
LSTM_X_test.shape:  (36718, 12, 98)
{'Model_number': '96', 'MAE': '12.9823379517', 'MSE': '341.8295288086', 'MAPE': '27132878.0000000000', 'Loss Function': 'MAE', 'Optimizer': 'Adamax', 'Learning Rate': '0.00100', 'Future_candles': 12, 'Window_size': 12, 'Dropout': '0.2', 'Epochs': '75', 'Batch Size': '256', 'Runtime': '12 min 15 seconds', 'Model type': 'LSTM', 'Number of hidden layers': 1, 'input_layer_LSTM': 128, '1_h_layer_LSTM_nodes': 256, '2_h_layer_LSTM_nodes': 0, '3_h_layer_LSTM_nodes': 0, 'Dense Layer': '1'}

pred_mean:  -0.29370565555878747
threshold_1: 9.570634971144113 , threshold_2: 19.141269942288226 , threshold_3: 28.71190491343234 , threshold_4: 38.28253988457645 

Initiating trading with threshold 1

BUY taken af idx: 13  date: 2020-01-01T21:10  pips gained: -7.9 
SELL taken af idx: 54  date: 2020-01-02T04:00  pips gained:

...

BUY taken af idx: 15040  date: 2020-05-29T03:10  pips gained: 35.3 
SELL taken af idx: 15059  date: 2020-05-29T06:20  pips gained: -7.7 
Entry price:  1.11332
stop loss activated, low: 1.11119
BUY taken af idx: 15177  date: 2020-06-01T04:00  pips gained: -22.0 
Entry price:  1.11639
stop loss activated, high: 1.11847
SELL taken af idx: 15323  date: 2020-06-02T04:20  pips gained: -22.0 
BUY taken af idx: 15355  date: 2020-06-02T09:40  pips gained: 2.5 
SELL taken af idx: 15373  date: 2020-06-02T12:40  pips gained: 11.2 
SELL taken af idx: 15423  date: 2020-06-02T21:00  pips gained: 2.5 
SELL taken af idx: 15448  date: 2020-06-03T01:10  pips gained: -14.9 
Entry price:  1.12061
stop loss activated, low: 1.11838
BUY taken af idx: 15480  date: 2020-06-03T06:30  pips gained: -22.0 
SELL taken af idx: 15581  date: 2020-06-03T23:20  pips gained: -4.9 
Entry price:  1.1244399999999999
stop loss activated, high: 1.12721
SELL taken af idx: 15631  date: 2020-06-04T07:40  pips gained: -22.0 
BUY t

Entry price:  1.1730399999999999
stop loss activated, high: 1.17535
SELL taken af idx: 21154  date: 2020-07-29T08:30  pips gained: -22.0 
BUY taken af idx: 21260  date: 2020-07-30T02:10  pips gained: -0.4 
Entry price:  1.1777
stop loss activated, high: 1.18097
SELL taken af idx: 21300  date: 2020-07-30T08:50  pips gained: -22.0 
SELL taken af idx: 21328  date: 2020-07-30T13:30  pips gained: -14.7 
BUY taken af idx: 21385  date: 2020-07-30T23:00  pips gained: 2.6 
SELL taken af idx: 21411  date: 2020-07-31T03:20  pips gained: 45.2 
SELL taken af idx: 21424  date: 2020-07-31T05:30  pips gained: 16.0 
Entry price:  1.18218
stop loss activated, low: 1.1786
BUY taken af idx: 21462  date: 2020-07-31T11:50  pips gained: -22.0 
BUY taken af idx: 21488  date: 2020-07-31T16:10  pips gained: 6.6 
SELL taken af idx: 21513  date: 2020-08-02T22:20  pips gained: -13.5 
SELL taken af idx: 21549  date: 2020-08-03T04:20  pips gained: 49.7 
BUY taken af idx: 21578  date: 2020-08-03T09:10  pips gained: 3

SELL taken af idx: 31369  date: 2020-11-06T10:20  pips gained: -5.1 
BUY taken af idx: 31384  date: 2020-11-06T12:50  pips gained: -1.5 
BUY taken af idx: 31416  date: 2020-11-08T20:10  pips gained: 1.6 
Entry price:  1.18865
stop loss activated, low: 1.1864700000000001
BUY taken af idx: 31455  date: 2020-11-09T02:40  pips gained: -22.0 
BUY taken af idx: 31477  date: 2020-11-09T06:20  pips gained: 14.9 
BUY taken af idx: 31505  date: 2020-11-09T11:00  pips gained: 9.1 
BUY taken af idx: 31590  date: 2020-11-10T01:10  pips gained: -2.6 
SELL taken af idx: 31612  date: 2020-11-10T04:50  pips gained: 3.7 
SELL taken af idx: 31626  date: 2020-11-10T07:10  pips gained: 7.6 
BUY taken af idx: 31640  date: 2020-11-10T09:30  pips gained: -6.3 
BUY taken af idx: 31746  date: 2020-11-11T03:10  pips gained: -4.8 
BUY taken af idx: 32468  date: 2020-11-18T05:30  pips gained: -17.1 
SELL taken af idx: 32495  date: 2020-11-18T10:00  pips gained: -4.0 
SELL taken af idx: 32510  date: 2020-11-18T12:3

SELL taken af idx: 8794  date: 2020-03-30T01:50  pips gained: 16.0 
Entry price:  1.0991
stop loss activated, high: 1.10162
SELL taken af idx: 9002  date: 2020-03-31T12:30  pips gained: -22.0 
BUY taken af idx: 9182  date: 2020-04-01T18:30  pips gained: -9.7 
SELL taken af idx: 9281  date: 2020-04-02T11:00  pips gained: 18.2 
BUY taken af idx: 9505  date: 2020-04-06T02:20  pips gained: -11.8 
BUY taken af idx: 9518  date: 2020-04-06T04:30  pips gained: 13.9 
Entry price:  1.0790799999999998
stop loss activated, low: 1.07683
BUY taken af idx: 9540  date: 2020-04-06T08:10  pips gained: -22.0 
BUY taken af idx: 9554  date: 2020-04-06T10:30  pips gained: 1.8 
BUY taken af idx: 9704  date: 2020-04-07T11:30  pips gained: 3.2 
BUY taken af idx: 9792  date: 2020-04-08T02:10  pips gained: 15.1 
Entry price:  1.0887799999999999
stop loss activated, low: 1.0867
BUY taken af idx: 10537  date: 2020-04-15T08:20  pips gained: -22.0 
SELL taken af idx: 10841  date: 2020-04-17T11:00  pips gained: 11.5 

SELL taken af idx: 32643  date: 2020-11-19T10:40  pips gained: -4.9 
BUY taken af idx: 32786  date: 2020-11-20T10:30  pips gained: -11.5 
Entry price:  1.18517
stop loss activated, high: 1.18741
SELL taken af idx: 33055  date: 2020-11-24T09:20  pips gained: -22.0 
BUY taken af idx: 33745  date: 2020-12-02T03:20  pips gained: 6.3 
SELL taken af idx: 33932  date: 2020-12-03T10:30  pips gained: 22.1 
BUY taken af idx: 34226  date: 2020-12-07T13:30  pips gained: -10.0 
BUY taken af idx: 34777  date: 2020-12-11T09:20  pips gained: -12.3 
BUY taken af idx: 35246  date: 2020-12-16T17:30  pips gained: -4.2 
Entry price:  1.21865
stop loss activated, high: 1.22163
SELL taken af idx: 35903  date: 2020-12-23T09:00  pips gained: -22.0 
SELL taken af idx: 36053  date: 2020-12-24T10:00  pips gained: 5.7 
Entry price:  1.22119
stop loss activated, low: 1.2191299999999998
BUY taken af idx: 36220  date: 2020-12-28T06:00  pips gained: -22.0 
SELL taken af idx: 36384  date: 2020-12-29T09:20  pips gained: